# Wykład 03 - notatnik

In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go

# Przygotowanie i analiza danych
Naszym celem jest przewidzieć czy inwestycja się uda, a kredytobiorca zwróci kredyt.

Link do danych: https://www.dropbox.com/s/spzn2s7anh7tnn9/jaypeedevlin-lending-club-loan-data-2007-11.zip?dl=0

Mamy do dyspozycji dwa pliki

* lending_club_loans.csv – zawiera dane
* LCDataDictionary.csv – zawiera opis poszczególnych kolumn

Nasz zbiór danych zawiera informacje o bieżących kredytach, spłaconych pożyczkach i niespłacanych pożyczkach.

In [94]:
pd.set_option('max_columns', 120)
pd.set_option('max_colwidth', 5000)

Ustawiamy kilka parametrów, które ułatwią nam zczytanie danych:

* Usuwamy pierwszą linię: zawiera zbędny tekst zamiast tytułów kolumn.
* Usuwamy kolumnę ‘desc’: zawiera długie wyjaśnienie dotyczące pożyczki.
* Usuwamy kolumnę ‘url’: zawiera link do każdego z Klubów Kredytowych.
* Usunięcie wszystkich kolumn o więcej niż 50% brakujących wartościach: Pozwala to na szybsze poruszanie się, ponieważ nie trzeba poświęcać czasu na próby wypełnienia tych wartości.

In [95]:
loans_2007 = pd.read_csv('./Dane/lending_club_loans.csv', skiprows=1, low_memory=False)
half_count = len(loans_2007) / 2
loans_2007 = loans_2007.dropna(thresh=half_count,axis=1) # Drop any column with more than 50% missing values
loans_2007 = loans_2007.drop(['url','desc'],axis=1)      # These columns are not useful for our purposes

In [96]:
print(loans_2007.shape)
loans_2007.head(3)

(42538, 56)


id  member_id  loan_amnt  funded_amnt  funded_amnt_inv        term  \
0  1077501  1296599.0     5000.0       5000.0           4975.0   36 months   
1  1077430  1314167.0     2500.0       2500.0           2500.0   60 months   
2  1077175  1313524.0     2400.0       2400.0           2400.0   36 months   

  int_rate  installment grade sub_grade emp_title emp_length home_ownership  \
0   10.65%       162.87     B        B2       NaN  10+ years           RENT   
1   15.27%        59.83     C        C4     Ryder   < 1 year           RENT   
2   15.96%        84.33     C        C5       NaN  10+ years           RENT   

   annual_inc verification_status   issue_d  loan_status pymnt_plan  \
0     24000.0            Verified  Dec-2011   Fully Paid          n   
1     30000.0     Source Verified  Dec-2011  Charged Off          n   
2     12252.0        Not Verified  Dec-2011   Fully Paid          n   

          purpose                 title zip_code addr_state    dti  \
0     credit_card              Computer    860xx         AZ  27.65   
1             car                  bike    309xx         GA   1.00   
2  small_business  real estate business    606xx         IL   8.72   

   delinq_2yrs earliest_cr_line  fico_range_low  fico_range_high  \
0          0.0         Jan-1985           735.0            739.0   
1          0.0         Apr-1999           740.0            744.0   
2          0.0         Nov-2001           735.0            739.0   

   inq_last_6mths  open_acc  pub_rec  revol_bal revol_util  total_acc  \
0             1.0       3.0      0.0    13648.0      83.7%        9.0   
1             5.0       3.0      0.0     1687.0       9.4%        4.0   
2             2.0       2.0      0.0     2956.0      98.5%       10.0   

  initial_list_status  out_prncp  out_prncp_inv  total_pymnt  total_pymnt_inv  \
0                   f        0.0            0.0  5863.155187          5833.84   
1                   f        0.0            0.0  1008.710000          1008.71   
2                   f        0.0            0.0  3005.666844          3005.67   

   total_rec_prncp  total_rec_int  total_rec_late_fee  recoveries  \
0          5000.00         863.16                 0.0        0.00   
1           456.46         435.17                 0.0      117.08   
2          2400.00         605.67                 0.0        0.00   

   collection_recovery_fee last_pymnt_d  last_pymnt_amnt last_credit_pull_d  \
0                     0.00     Jan-2015           171.62           Sep-2016   
1                     1.11     Apr-2013           119.66           Sep-2016   
2                     0.00     Jun-2014           649.91           Sep-2016   

   last_fico_range_high  last_fico_range_low  collections_12_mths_ex_med  \
0                 744.0                740.0                         0.0   
1                 499.0                  0.0                         0.0   
2                 719.0                715.0                         0.0   

   policy_code application_type  acc_now_delinq  chargeoff_within_12_mths  \
0          1.0       INDIVIDUAL             0.0                       0.0   
1          1.0       INDIVIDUAL             0.0                       0.0   
2          1.0       INDIVIDUAL             0.0                       0.0   

   delinq_amnt  pub_rec_bankruptcies  tax_liens  
0          0.0                   0.0        0.0  
1          0.0                   0.0        0.0  
2          0.0                   0.0        0.0

## Musimy zapoznać się z kolumnami w zbiorze danych

Aby zrozumieć całą tabelę musimy zrozumieć co reprezentuje każda cecha. Jest to istotne dla procesu modelowania danych.
Nasz słownik znajduje się w ./Dane/LCDataDictionary.csv

In [97]:
data_dictionary = pd.read_csv('./Dane/LCDataDictionary.csv') # Loading in the data dictionary
print(data_dictionary.shape[0])
print(data_dictionary.columns.tolist())

117
['LoanStatNew', 'Description']


In [98]:
data_dictionary = data_dictionary.rename(columns={'LoanStatNew': 'name','Description': 'description'})
data_dictionary.head()

name  \
0        acc_now_delinq   
1  acc_open_past_24mths   
2            addr_state   
3              all_util   
4            annual_inc   

                                                                     description  
0                The number of accounts on which the borrower is now delinquent.  
1                                     Number of trades opened in past 24 months.  
2                     The state provided by the borrower in the loan application  
3                                          Balance to credit limit on all trades  
4  The self-reported annual income provided by the borrower during registration.

## Tworzymy DataFrame z nazwami kolumn i ich opisami
Teraz, gdy mamy ładny słownik danych, dodajemy do niego pierwszy wiersz z przykładowymi wartościami (żeby widzieć jaki mają format) oraz tworzymy DataFrame żeby mieć dobry dostęp do danych z nazwami kolumn:

* name - zawiera nazwy kolumn naszego pliku.
* dtypes - zawiera typy danych w kolumnach.
* first value - zawiera wartości pierwszego rzędu danych.
* description - wyjaśnia, co oznacza każda kolumna danych.

In [99]:
loans_2007_dtypes = pd.DataFrame(loans_2007.dtypes,columns=['dtypes'])
loans_2007_dtypes = loans_2007_dtypes.reset_index()
loans_2007_dtypes['name'] = loans_2007_dtypes['index']
loans_2007_dtypes = loans_2007_dtypes[['name','dtypes']]

loans_2007_dtypes['first value'] = loans_2007.loc[0].values
preview = loans_2007_dtypes.merge(data_dictionary, on='name',how='left')

In [100]:
preview

name   dtypes  first value  \
0                           id   object      1077501   
1                    member_id  float64    1296599.0   
2                    loan_amnt  float64       5000.0   
3                  funded_amnt  float64       5000.0   
4              funded_amnt_inv  float64       4975.0   
5                         term   object    36 months   
6                     int_rate   object       10.65%   
7                  installment  float64       162.87   
8                        grade   object            B   
9                    sub_grade   object           B2   
10                   emp_title   object          NaN   
11                  emp_length   object    10+ years   
12              home_ownership   object         RENT   
13                  annual_inc  float64      24000.0   
14         verification_status   object     Verified   
15                     issue_d   object     Dec-2011   
16                 loan_status   object   Fully Paid   
17                  pymnt_plan   object            n   
18                     purpose   object  credit_card   
19                       title   object     Computer   
20                    zip_code   object        860xx   
21                  addr_state   object           AZ   
22                         dti  float64        27.65   
23                 delinq_2yrs  float64          0.0   
24            earliest_cr_line   object     Jan-1985   
25              fico_range_low  float64        735.0   
26             fico_range_high  float64        739.0   
27              inq_last_6mths  float64          1.0   
28                    open_acc  float64          3.0   
29                     pub_rec  float64          0.0   
30                   revol_bal  float64      13648.0   
31                  revol_util   object        83.7%   
32                   total_acc  float64          9.0   
33         initial_list_status   object            f   
34                   out_prncp  float64          0.0   
35               out_prncp_inv  float64          0.0   
36                 total_pymnt  float64  5863.155187   
37             total_pymnt_inv  float64      5833.84   
38             total_rec_prncp  float64       5000.0   
39               total_rec_int  float64       863.16   
40          total_rec_late_fee  float64          0.0   
41                  recoveries  float64          0.0   
42     collection_recovery_fee  float64          0.0   
43                last_pymnt_d   object     Jan-2015   
44             last_pymnt_amnt  float64       171.62   
45          last_credit_pull_d   object     Sep-2016   
46        last_fico_range_high  float64        744.0   
47         last_fico_range_low  float64        740.0   
48  collections_12_mths_ex_med  float64          0.0   
49                 policy_code  float64          1.0   
50            application_type   object   INDIVIDUAL   
51              acc_now_delinq  float64          0.0   
52    chargeoff_within_12_mths  float64          0.0   
53                 delinq_amnt  float64          0.0   
54        pub_rec_bankruptcies  float64          0.0   
55                   tax_liens  float64          0.0   

                                                                                                                                                                                                 description  
0                                                                                                                                                              A unique LC assigned ID for the loan listing.  
1                                                                                                                                                           A unique LC assigned Id for the borrower member.  
2                               The listed amount of the loan applied for by the borrower. If at some point in time, the credit department reduces the loan amount, then it will be reflected in this value.  
3    

## Usuwanie zbędnych kolumn
Podczas przeglądania kolumn warto zwrócić uwagę na kolumny, które:

* ujawniają informacje z przyszłości np. po udzieleniu pożyczki (information leaks),
* nie mają wpływu na badane zmienne (np. Losowo wygenerowane wartości id),
* są źle sformatowane
* są ciężkie do przerobienia na format liczbowy,
* zawierają zbędne informacje.

## Analiza własna kolumn do usunięcia

Poniższe kolumny są niepotrzebne:
(0-19)
* id
* member_id
* emp_title
* funded_amnt
* funded_amnt_inv
* issue_d

(19-38)
* zip_code
* adrr_state
* dti

(38-55)
* last_pymnt_d
* last_pymnt_amnt
* last_credit_pull_d
* acc_now_delinq
* delinq_amnt

### Wg. wykładu
(0-19)
* id - losowo generowane pole
* member_id - również losowo generowane pole
* funded_amnt - ujawnia informacje z przyszłości (po tym, jak pożyczka została już uruchomiona).
* funded_amnt_inv - także ujawnia dane z przyszłości.
* sub_grade - zawiera nadmiarowe informacje, które znajdują się już w kolumnie grade
* int_rate - również zawiera się w kolumnie grade.
* emp_title - wymaga dużo przetwarzania, aby stać się potencjalnie użyteczna
* issued_d - wyciek danych z przyszłości.

(19-38)
* zip_code - informacja zawiera się w kolumnie addr_state (ponieważ widoczne są tylko pierwsze 3 cyfry 5-cyfrowego kodu pocztowego).
* out_prncp - wyciek danych z przyszłości.
* out_prncp_inv - także wyciek danych z przyszłości.
* total_pymnt - także wyciek danych z przyszłości.
* total_pymnt_inv - także wyciek danych z przyszłości.

(38-55)
Dane odnoszą się do przyszłości
* total_rec_prncp
* total_rec_int
* total_rec_late_fee
* recoveries
* collection_recovery_fee
* last_pymnt_d
* last_pymnt_amnt

In [101]:
drop_list = ['id','member_id','funded_amnt','funded_amnt_inv',
             'int_rate','sub_grade','emp_title','issue_d']
loans_2007 = loans_2007.drop(drop_list,axis=1)
drop_cols = [ 'zip_code','out_prncp','out_prncp_inv',
             'total_pymnt','total_pymnt_inv']
loans_2007 = loans_2007.drop(drop_cols, axis=1)
drop_cols = ['total_rec_prncp','total_rec_int', 'total_rec_late_fee',
             'recoveries', 'collection_recovery_fee', 'last_pymnt_d',
             'last_pymnt_amnt']

loans_2007 = loans_2007.drop(drop_cols, axis=1)

## Zajmijmy się bliżej kolumnami fico_range_low, fico_range_high, last_fico_range_low, last_fico_range_high.
Wyniki FICO to ocena kredytowa czyli wartość liczbowa używana przez banki i instytucje kredytowe do określania wiarygodności osoby. Choć w Stanach Zjednoczonych jest kilka takich miar to FICO jest najbardziej znana i najczęściej używana.

Kiedy kredytobiorca ubiegający się o pożyczkę uzyskuje ocenę kredytową FICO - otrzymuje dolną i górną granicę zakresu, do której należy (fico_range_low, fico_range_high). Następnie wszystkie aktualizacje wyników kredytobiorców są rejestrowane jako last_fico_range_low i last_fico_range_high.

### Kluczową częścią każdego projektu w dziedzinie analizy danych jest zrobienie wszystkiego aby zrozumieć dane.
Badając nasze dane, można odnieść się do innych projektów, które je analizowały. W 2014 roku grupa studentów z Uniwersytetu Stanford w raporcie (http://cs229.stanford.edu/proj2014/Kevin%20Tsai,Sivagami%20Ramiah,Sudhanshu%20Singh,Peer%20Lending%20Risk%20Predictor.pdf) wymieniła last_fico_range jako czynnik, który powoduje użycie informacji z przyszłości.

Natomiast inna grupa ze Stanford pracująca nad tymi samymi danymi wykorzystała tę kolumnę w swoich modelach. W raporcie z tej drugiej grupy (http://cs229.stanford.edu/proj2015/199_report.pdf) opisano last_fico_range_high jako jedną z ważniejszych kolumn umożliwiającą predykcję.

Pytanie, na które musimy odpowiedzieć, to czy informacje o wyniku kredytowym FICO używają informacji z przyszłości? Przypomnijmy, że kolumna jest uważana za wyciek informacji, gdy w szczególności nie będzie ona dostępna w momencie korzystania z naszego modelu - w tym przypadku, gdy używamy naszego modelu dotyczącego przyszłych pożyczek.

Ten blog (https://www.peercube.com/blog/post/fico-score-trends-and-defaults-for-lending-club-loans) który analizuje wyniki FICO dotyczące udzielania pożyczek, twierdzi że nasza kolumna jest świetnym predyktorem tego, czy pożyczka będzie spłacona, ponieważ wyniki FICO są aktualizowane po udzieleniu pożyczki.

Ponadto twierdzą, że powinno się używać średniej wartości fico_range_low i fico_range_high.

### Dlatego możemy bezpiecznie używać fico_range_low i fico_range_high, ale nie last_fico_range_low i last_fico_range_high.

In [102]:
print(loans_2007['fico_range_low'].unique())
print(loans_2007['fico_range_high'].unique())

[735. 740. 690. 695. 730. 660. 675. 725. 710. 705. 720. 665. 670. 760.
 685. 755. 680. 700. 790. 750. 715. 765. 745. 770. 780. 775. 795. 810.
 800. 815. 785. 805. 825. 820. 630. 625.  nan 650. 655. 645. 640. 635.
 610. 620. 615.]
[739. 744. 694. 699. 734. 664. 679. 729. 714. 709. 724. 669. 674. 764.
 689. 759. 684. 704. 794. 754. 719. 769. 749. 774. 784. 779. 799. 814.
 804. 819. 789. 809. 829. 824. 634. 629.  nan 654. 659. 649. 644. 639.
 614. 624. 619.]


## Brakujące wartości
Pozbądźmy się brakujących wartości, a następnie narysujmy histogramy dla tych kolumn:

In [103]:
fico_columns = ['fico_range_high','fico_range_low']
print(loans_2007.shape[0])

loans_2007.dropna(subset=fico_columns,inplace=True)
print(loans_2007.shape[0])

42538
42535


In [104]:
hist = px.histogram(loans_2007[['fico_range_high', 'fico_range_low', ]], nbins=200, barmode="overlay", marginal='box')
# hist.add_trace(histogram(loans_2007['fico_range_high']))
hist.show()

## Weźmy średnią tych kolumn

In [105]:
loans_2007['fico_average'] = (loans_2007['fico_range_high'] + loans_2007['fico_range_low']) / 2
cols = ['fico_range_low','fico_range_high','fico_average']
loans_2007[cols].head()

fico_range_low  fico_range_high  fico_average
0           735.0            739.0         737.0
1           740.0            744.0         742.0
2           735.0            739.0         737.0
3           690.0            694.0         692.0
4           695.0            699.0         697.0

Średnia wystarcza nam do potrzeb predykcji - dropujemy kolmuny niepotrzebne

In [106]:
drop_cols = ['fico_range_low','fico_range_high','last_fico_range_low',
             'last_fico_range_high']
loans_2007 = loans_2007.drop(drop_cols, axis=1)
loans_2007.shape

(42535, 33)

Tym sposobem zmniejszyliśmy liczbę kolumn do z 56 do 33.



### Pamiętaj, że głównym celem jest przewidzenie, kto spłaci pożyczkę, a kto nie.
Na podstawie danych dowiedzieliśmy się, że loan_status jest jedyną kolumną, która opisuje stan kredytu, dlatego skorzystaj z tej kolumny jako kolumny docelowej.

In [107]:
preview[preview.name=='loan_status']

name  dtypes first value                 description
16  loan_status  object  Fully Paid  Current status of the loan

Aktualnie ta kolumna zawiera wartości tekstowe, które muszą zostać przeliczone na wartości liczbowe, które mogą być użyte w modelu.

Zbadajmy różne wartości w tej kolumnie i zaproponujemy strategię konwersji wartości w tej kolumnie. Użyjemy metody DataFrame value_counts(), aby zwrócić ilość wystąpień unikalnych wartości w kolumnie loan_status.

In [108]:
loans_2007["loan_status"].value_counts()

Fully Paid                                             33586
Charged Off                                             5653
Does not meet the credit policy. Status:Fully Paid      1988
Does not meet the credit policy. Status:Charged Off      761
Current                                                  513
In Grace Period                                           16
Late (31-120 days)                                        12
Late (16-30 days)                                          5
Default                                                    1
Name: loan_status, dtype: int64

Dopiszmy znaczenia kolumn

In [109]:
meaning = [
    "Loan has been fully paid off.",
    "Loan for which there is no longer a reasonable expectation of further payments.",
    "While the loan was paid off, the loan application today would no longer meet the credit policy and wouldn't be approved on to the marketplace.",
    "While the loan was charged off, the loan application today would no longer meet the credit policy and wouldn't be approved on to the marketplace.",
    "Loan is up to date on current payments.",
    "The loan is past due but still in the grace period of 15 days.",
    "Loan hasn't been paid in 31 to 120 days (late on the current payment).",
    "Loan hasn't been paid in 16 to 30 days (late on the current payment).",
    "Loan is defaulted on and no payment has been made for more than 121 days."]

status, count = loans_2007["loan_status"].value_counts().index, loans_2007["loan_status"].value_counts().values

loan_statuses_explanation = pd.DataFrame({'Loan Status': status,'Count': count,'Meaning': meaning})[['Loan Status','Count','Meaning']]
loan_statuses_explanation

Loan Status  Count  \
0                                           Fully Paid  33586   
1                                          Charged Off   5653   
2   Does not meet the credit policy. Status:Fully Paid   1988   
3  Does not meet the credit policy. Status:Charged Off    761   
4                                              Current    513   
5                                      In Grace Period     16   
6                                   Late (31-120 days)     12   
7                                    Late (16-30 days)      5   
8                                              Default      1   

                                                                                                                                             Meaning  
0                                                                                                                      Loan has been fully paid off.  
1                                                                    Loan for which there is no longer a reasonable expectation of further payments.  
2     While the loan was paid off, the loan application today would no longer meet the credit policy and wouldn't be approved on to the marketplace.  
3  While the loan was charged off, the loan application today would no longer meet the credit policy and wouldn't be approved on to the marketplace.  
4                                                                                                            Loan is up to date on current payments.  
5                                                                                     The loan is past due but still in the grace period of 15 days.  
6                                                                             Loan hasn't been paid in 31 to 120 days (late on the current payment).  
7                                                                              Loan hasn't been paid in 16 to 30 days (late on the current payment).  
8                                                                          Loan is defaulted on and no payment has been made for more than 121 days.

### Pamiętajmy, że naszym celem jest zbudowanie modelu opisującego kredyty, które zostaną spłacone lub nie.
Z powyższej tabeli wynika, że w kolumnach Fully Paid oraz Charged Off mamy dokładnie te informacje. Pozostałe wartości opisują kredyty w trakcie realizacji.

Usuńmy wszystkie wiersze, które nie zawierają wartości Fully Paid oraz Charged Off, a następnie przekształcamy wartości na dane liczbowe 0, 1.

In [110]:
loans_2007 = loans_2007[(loans_2007["loan_status"] == "Fully Paid") |
                            (loans_2007["loan_status"] == "Charged Off")]

mapping_dictionary = {"loan_status":{ "Fully Paid": 1, "Charged Off": 0}}
loans_2007 = loans_2007.replace(mapping_dictionary)

In [115]:
filtered_loans=loans_2007
print(filtered_loans.shape)
filtered_loans.head()

(39239, 33)


loan_amnt        term  installment grade emp_length home_ownership  \
0     5000.0   36 months       162.87     B  10+ years           RENT   
1     2500.0   60 months        59.83     C   < 1 year           RENT   
2     2400.0   36 months        84.33     C  10+ years           RENT   
3    10000.0   36 months       339.31     C  10+ years           RENT   
5     5000.0   36 months       156.46     A    3 years           RENT   

   annual_inc verification_status  loan_status pymnt_plan         purpose  \
0     24000.0            Verified            1          n     credit_card   
1     30000.0     Source Verified            0          n             car   
2     12252.0        Not Verified            1          n  small_business   
3     49200.0     Source Verified            1          n           other   
5     36000.0     Source Verified            1          n         wedding   

                                   title addr_state    dti  delinq_2yrs  \
0                               Computer         AZ  27.65          0.0   
1                                   bike         GA   1.00          0.0   
2                   real estate business         IL   8.72          0.0   
3                               personel         CA  20.00          0.0   
5  My wedding loan I promise to pay back         AZ  11.20          0.0   

  earliest_cr_line  inq_last_6mths  open_acc  pub_rec  revol_bal revol_util  \
0         Jan-1985             1.0       3.0      0.0    13648.0      83.7%   
1         Apr-1999             5.0       3.0      0.0     1687.0       9.4%   
2         Nov-2001             2.0       2.0      0.0     2956.0      98.5%   
3         Feb-1996             1.0      10.0      0.0     5598.0        21%   
5         Nov-2004             3.0       9.0      0.0     7963.0      28.3%   

   total_acc initial_list_status last_credit_pull_d  \
0        9.0                   f           Sep-2016   
1        4.0                   f           Sep-2016   
2       10.0                   f           Sep-2016   
3       37.0                   f           Apr-2016   
5       12.0                   f           Jan-2016   

   collections_12_mths_ex_med  policy_code application_type  acc_now_delinq  \
0                         0.0          1.0       INDIVIDUAL             0.0   
1                         0.0          1.0       INDIVIDUAL             0.0   
2                         0.0          1.0       INDIVIDUAL             0.0   
3                         0.0          1.0       INDIVIDUAL             0.0   
5                         0.0          1.0       INDIVIDUAL             0.0   

   chargeoff_within_12_mths  delinq_amnt  pub_rec_bankruptcies  tax_liens  \
0                       0.0          0.0                   0.0        0.0   
1                       0.0          0.0                   0.0        0.0   
2                       0.0          0.0                   0.0        0.0   
3                       0.0          0.0                   0.0        0.0   
5                       0.0          0.0                   0.0        0.0   

   fico_average  
0         737.0  
1         742.0  
2         737.0  
3         692.0  
5         732.0

Możemy zwizualizować nasze dane. Te wykresy wskazują, że znaczna liczba kredytów została spłacona - 85,62%.

In [119]:
fig = px.histogram(filtered_loans, x='loan_status',  color='loan_status')
fig.show()

fig = px.pie(filtered_loans, names='loan_status')
fig.show()

## Usuwanie kolumn tylko z jedną wartością
Przyjrzyjmy się kolumną zawierającym tylko jedną unikatową wartość i usuńmy je. Te kolumny nie będą przydatne dla modelu. Metoda nunique() zwraca liczbę unikalnych wartości. Możemy zastosować tę metodę w całym zbiorze danych w celu usunięcia ich.

In [121]:
loans_2007 = loans_2007.loc[:,loans_2007.apply(pd.Series.nunique) != 1]
loans_2007.shape

(39239, 25)

Może występować kilka kolumn zawierających więcej niż jedną unikatową wartość, ale jedna z wartości występuje znacznie częściej.

In [122]:
for col in loans_2007.columns:
    if (len(loans_2007[col].unique()) < 4):
        print(loans_2007[col].value_counts())
        print()

 36 months    29096
 60 months    10143
Name: term, dtype: int64

Not Verified       16845
Verified           12526
Source Verified     9868
Name: verification_status, dtype: int64

1    33586
0     5653
Name: loan_status, dtype: int64

n    39238
y        1
Name: pymnt_plan, dtype: int64



Kolumna planu płatności pymnt_plan przyjmuje tylko dwie unikatowe wartości (w tym jedna z nich występuje tylko raz), więc możemy ją usunąć.

In [123]:
print(loans_2007.shape[1])
loans_2007 = loans_2007.drop('pymnt_plan', axis=1)
print("We've been able to reduced the features to => {}".format(loans_2007.shape[1]))

25
We've been able to reduced the features to => 24


# Zapiszmy dane do pliku

In [124]:
loans_2007.to_csv("./Dane/filtered_loans_2007.csv",index=False)

### Ponowne wczytanie danych

In [140]:
filtered_loans = pd.read_csv('./Dane/filtered_loans_2007.csv', sep=',', encoding='latin-1')
print(filtered_loans.shape)
filtered_loans.head()

(39239, 24)


loan_amnt        term  installment grade emp_length home_ownership  \
0     5000.0   36 months       162.87     B  10+ years           RENT   
1     2500.0   60 months        59.83     C   < 1 year           RENT   
2     2400.0   36 months        84.33     C  10+ years           RENT   
3    10000.0   36 months       339.31     C  10+ years           RENT   
4     5000.0   36 months       156.46     A    3 years           RENT   

   annual_inc verification_status  loan_status         purpose  \
0     24000.0            Verified            1     credit_card   
1     30000.0     Source Verified            0             car   
2     12252.0        Not Verified            1  small_business   
3     49200.0     Source Verified            1           other   
4     36000.0     Source Verified            1         wedding   

                                   title addr_state    dti  delinq_2yrs  \
0                               Computer         AZ  27.65          0.0   
1                                   bike         GA   1.00          0.0   
2                   real estate business         IL   8.72          0.0   
3                               personel         CA  20.00          0.0   
4  My wedding loan I promise to pay back         AZ  11.20          0.0   

  earliest_cr_line  inq_last_6mths  open_acc  pub_rec  revol_bal revol_util  \
0         Jan-1985             1.0       3.0      0.0    13648.0      83.7%   
1         Apr-1999             5.0       3.0      0.0     1687.0       9.4%   
2         Nov-2001             2.0       2.0      0.0     2956.0      98.5%   
3         Feb-1996             1.0      10.0      0.0     5598.0        21%   
4         Nov-2004             3.0       9.0      0.0     7963.0      28.3%   

   total_acc last_credit_pull_d  pub_rec_bankruptcies  fico_average  
0        9.0           Sep-2016                   0.0         737.0  
1        4.0           Sep-2016                   0.0         742.0  
2       10.0           Sep-2016                   0.0         737.0  
3       37.0           Apr-2016                   0.0         692.0  
4       12.0           Jan-2016                   0.0         732.0

## Musimy usunąć brakujące wartości.
Po pierwsze, użyjemy metody isnull(), która zwraca ramkę danych z wartościami:

* True - jeśli pierwotna wartość jest null-em
* False - jeśli pierwotna wartość nie jest null-em

Następnie należy użyć metody sum() aby obliczyć liczbę wartości null w każdej kolumnie.

In [141]:
null_counts = filtered_loans.isnull().sum()
print("Number of null values in each column:\n{}".format(null_counts))

Number of null values in each column:
loan_amnt                  0
term                       0
installment                0
grade                      0
emp_length              1057
home_ownership             0
annual_inc                 0
verification_status        0
loan_status                0
purpose                    0
title                     11
addr_state                 0
dti                        0
delinq_2yrs                0
earliest_cr_line           0
inq_last_6mths             0
open_acc                   0
pub_rec                    0
revol_bal                  0
revol_util                50
total_acc                  0
last_credit_pull_d         2
pub_rec_bankruptcies     697
fico_average               0
dtype: int64


Usuwamy kolumny zawierające więcej niż 1% (392) wartości null. Ponadto usuwamy wszystkie wiersze zawierające nulle.

In [142]:
drop_list = ['pub_rec_bankruptcies']
filtered_loans = filtered_loans.drop(drop_list, axis=1)
filtered_loans = filtered_loans.dropna()

In [143]:
null_counts = filtered_loans.isnull().sum()
print("Number of null values in each column:\n{}".format(null_counts))

Number of null values in each column:
loan_amnt              0
term                   0
installment            0
grade                  0
emp_length             0
home_ownership         0
annual_inc             0
verification_status    0
loan_status            0
purpose                0
title                  0
addr_state             0
dti                    0
delinq_2yrs            0
earliest_cr_line       0
inq_last_6mths         0
open_acc               0
pub_rec                0
revol_bal              0
revol_util             0
total_acc              0
last_credit_pull_d     0
fico_average           0
dtype: int64


## Wszystkie kolumny muszą być reprezentowane jako kolumny numeryczne
Aby móc modelować dane wszystkie kolumny, muszą być reprezentowane jako kolumny numeryczne (typu int lub float). Wypiszmy teraz liczności kolumn ze względu na typ danych, jaki przechowują.

In [144]:
print("Data types and their frequency\n{}".format(filtered_loans.dtypes.value_counts()))

Data types and their frequency
float64    11
object     11
int64       1
dtype: int64


Mamy 11 kolumn zawierających tekst, które należy przekształcić do postaci numerycznej. Wybierzmy kolumny zawierające elementy typu object za pomocą funkcji select_dtype, a następnie wyświetl wiersz próbki, aby lepiej zrozumieć, jak sformatowane są wartości w każdej kolumnie.

In [145]:
object_columns_df = filtered_loans.select_dtypes(include=['object'])
print(object_columns_df.iloc[0])

term                     36 months
grade                            B
emp_length               10+ years
home_ownership                RENT
verification_status       Verified
purpose                credit_card
title                     Computer
addr_state                      AZ
earliest_cr_line          Jan-1985
revol_util                   83.7%
last_credit_pull_d        Sep-2016
Name: 0, dtype: object


Zauważ, że kolumna revol_util zawiera wartości numeryczne, ale jest sformatowana jako obiekt.
Musimy przekonwertować revol_util na wartości liczbowe.

Oto co powinniśmy zrobić:

1. możemy użyć metody str.rstrip(), aby usunąć procent (%).
2. na wynikowym obiekcie możemy użyć metody astype() aby przekonwertować wartość do typu float.
3. teraz możemy wynik zapisać do kolumny revol_util .

In [146]:
filtered_loans['revol_util'] = filtered_loans['revol_util'].str.rstrip('%').astype('float')

In [147]:
object_columns_df = filtered_loans.select_dtypes(include=['object'])
print(object_columns_df.iloc[0])

term                     36 months
grade                            B
emp_length               10+ years
home_ownership                RENT
verification_status       Verified
purpose                credit_card
title                     Computer
addr_state                      AZ
earliest_cr_line          Jan-1985
last_credit_pull_d        Sep-2016
Name: 0, dtype: object


### Kolumny:
* addr_state
* last_credit_pull_d
* earliest_cr_line
* title

zawierają bardzo różne wartości, które będzie trudno zamienić na dane numeryczne

In [148]:
strange_names = ['last_credit_pull_d','addr_state','title','earliest_cr_line']
for name in strange_names:
    print("Unique Values in column: {}\n".format(name))
    print(filtered_loans[name].value_counts(),'\n')

Unique Values in column: last_credit_pull_d

Sep-2016    14177
Mar-2016      805
Aug-2016      695
Feb-2013      657
Apr-2016      651
            ...  
May-2008        1
Jun-2008        1
Jul-2008        1
May-2007        1
Jul-2007        1
Name: last_credit_pull_d, Length: 110, dtype: int64 

Unique Values in column: addr_state

CA    6833
NY    3657
FL    2741
TX    2639
NJ    1802
IL    1476
PA    1460
VA    1359
GA    1340
MA    1292
OH    1167
MD    1020
AZ     819
WA     796
CO     755
NC     747
CT     719
MI     684
MO     653
MN     586
NV     473
SC     461
WI     433
OR     427
AL     424
LA     422
KY     315
OK     289
KS     253
UT     250
AR     232
DC     211
RI     195
NM     182
HI     166
WV     165
NH     159
DE     110
WY      79
MT      78
AK      77
SD      60
VT      53
MS      19
TN      17
IN       9
ID       6
IA       5
NE       5
ME       3
Name: addr_state, dtype: int64 

Unique Values in column: title

Debt Consolidation            2102
Debt Consolidati

Usuńmy je

In [149]:
filtered_loans = filtered_loans.drop(strange_names, axis=1)

In [150]:
object_columns_df = filtered_loans.select_dtypes(include=['object'])
print(object_columns_df.iloc[0])

term                     36 months
grade                            B
emp_length               10+ years
home_ownership                RENT
verification_status       Verified
purpose                credit_card
Name: 0, dtype: object


## Dane kategoryczne
Niektóre wartości kategoryczne są w naturalnej kolejności/porządku. Można te dane sortować/porządkować w kolejności rosnącej/malejącej np. w kolumnie grade przydzielona jest ocena od A do G gdzie A oznacza mniej ryzykowaną inwestycję niż B.
$$A<B<C<D<E<F<G$$

Niektórych wartości nominalnych nie można uporządkować np. kolumna purpose. Nie można napisać:
$$car<wedding<education<\dots$$

## Dane uporządkowane

Rozważamy kolumny:

* grade
* emp_length

Aby odwzorować wartości porządkowe na liczbę całkowitą, możemy użyć metody replace() :

In [151]:
mapping_dict = {
    "emp_length": {
        "10+ years": 10,
        "9 years": 9,
        "8 years": 8,
        "7 years": 7,
        "6 years": 6,
        "5 years": 5,
        "4 years": 4,
        "3 years": 3,
        "2 years": 2,
        "1 year": 1,
        "< 1 year": 0,
        "n/a": 0

    },
    "grade":{
        "A": 1,
        "B": 2,
        "C": 3,
        "D": 4,
        "E": 5,
        "F": 6,
        "G": 7
    }
}

filtered_loans = filtered_loans.replace(mapping_dict)
filtered_loans[['emp_length','grade']].head()

emp_length  grade
0          10      2
1           0      3
2          10      3
3          10      3
4           3      1

## Dane nieuporządkowane
Rozważamy kolumny:

* home_ownership
* verification_status
* purpose
* term

Przejdźmy do wartości nominalnych. Podejście do przekształcania cech nominalnych w cechy numeryczne polega na kodowaniu ich jako dummy variables. Czyli:
* za pomocą metody get_dummies () aby stworzyć reprezentację (http://pandas.pydata.org/pandas-docs/stable/generated/pandas.get_dummies.html)
* następnie za pomocą metody concat() aby dodać nowe kolumny do danych
* na koniec usuwamy stare kolumny

In [152]:
nominal_columns = ["home_ownership", "verification_status", "purpose", "term"]
dummy_df = pd.get_dummies(filtered_loans[nominal_columns])
print(dummy_df)
filtered_loans = pd.concat([filtered_loans, dummy_df], axis=1)
filtered_loans = filtered_loans.drop(nominal_columns, axis=1)

       home_ownership_MORTGAGE  home_ownership_NONE  home_ownership_OTHER  \
0                            0                    0                     0   
1                            0                    0                     0   
2                            0                    0                     0   
3                            0                    0                     0   
4                            0                    0                     0   
...                        ...                  ...                   ...   
39234                        1                    0                     0   
39235                        0                    0                     0   
39236                        1                    0                     0   
39237                        1                    0                     0   
39238                        0                    0                     0   

       home_ownership_OWN  home_ownership_RENT  \
0                       0

In [153]:
filtered_loans.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 38123 entries, 0 to 39238
Data columns (total 39 columns):
 #   Column                               Non-Null Count  Dtype  
---  ------                               --------------  -----  
 0   loan_amnt                            38123 non-null  float64
 1   installment                          38123 non-null  float64
 2   grade                                38123 non-null  int64  
 3   emp_length                           38123 non-null  int64  
 4   annual_inc                           38123 non-null  float64
 5   loan_status                          38123 non-null  int64  
 6   dti                                  38123 non-null  float64
 7   delinq_2yrs                          38123 non-null  float64
 8   inq_last_6mths                       38123 non-null  float64
 9   open_acc                             38123 non-null  float64
 10  pub_rec                              38123 non-null  float64
 11  revol_bal                   

Zapiszmy finalny wynik analizy danych do pliku:

In [154]:
filtered_loans.to_csv("./Dane/cleaned_loans_2007.csv",index=False)

## Ponowne wczytanie danych

In [155]:
cleaned_loans = pd.read_csv('./Dane/cleaned_loans_2007.csv', sep=',', encoding='latin-1')
print(cleaned_loans.shape)
cleaned_loans.head()

(38123, 39)


loan_amnt  installment  grade  emp_length  annual_inc  loan_status    dti  \
0     5000.0       162.87      2          10     24000.0            1  27.65   
1     2500.0        59.83      3           0     30000.0            0   1.00   
2     2400.0        84.33      3          10     12252.0            1   8.72   
3    10000.0       339.31      3          10     49200.0            1  20.00   
4     5000.0       156.46      1           3     36000.0            1  11.20   

   delinq_2yrs  inq_last_6mths  open_acc  pub_rec  revol_bal  revol_util  \
0          0.0             1.0       3.0      0.0    13648.0        83.7   
1          0.0             5.0       3.0      0.0     1687.0         9.4   
2          0.0             2.0       2.0      0.0     2956.0        98.5   
3          0.0             1.0      10.0      0.0     5598.0        21.0   
4          0.0             3.0       9.0      0.0     7963.0        28.3   

   total_acc  fico_average  home_ownership_MORTGAGE  home_ownership_NONE  \
0        9.0         737.0                        0                    0   
1        4.0         742.0                        0                    0   
2       10.0         737.0                        0                    0   
3       37.0         692.0                        0                    0   
4       12.0         732.0                        0                    0   

   home_ownership_OTHER  home_ownership_OWN  home_ownership_RENT  \
0                     0                   0                    1   
1                     0                   0                    1   
2                     0                   0                    1   
3                     0                   0                    1   
4                     0                   0                    1   

   verification_status_Not Verified  verification_status_Source Verified  \
0                                 0                                    0   
1                                 0                                    1   
2                                 1                                    0   
3                                 0                                    1   
4                                 0                                    1   

   verification_status_Verified  purpose_car  purpose_credit_card  \
0                             1            0                    1   
1                             0            1                    0   
2                             0            0                    0   
3                             0            0                    0   
4                             0            0                    0   

   purpose_debt_consolidation  purpose_educational  purpose_home_improvement  \
0                           0                    0                         0   
1                           0                    0                         0   
2                           0                    0                         0   
3                           0                    0                         0   
4                           0                    0                         0   

   purpose_house  purpose_major_purchase  purpose_medical  purpose_moving  \
0              0                       0                0               0   
1              0                       0                0               0   
2              0                       0                0               0   
3              0                       0                0               0   
4              0                       0                0               0   

   purpose_other  purpose_renewable_energy  purpose_small_business  \
0              0                         0                       0   
1              0                         0                       0   
2              0                         0                       1   
3              1                         0                       0   
4              0                 

## Przeanalizujmy korelację danych:

In [158]:
corr = cleaned_loans.corr()

mask = np.zeros_like(corr, np.bool_)
mask[np.triu_indices_from(mask)] = True
mask = ~mask

heat = px.imshow(corr*mask)
heat.show()

Zabawa z ręcznym dopasowaniem modelu

In [164]:
from sklearn import datasets
from sklearn.model_selection import cross_val_predict
from sklearn import datasets, linear_model
from sklearn.preprocessing import PolynomialFeatures
from sklearn.pipeline import make_pipeline
from sklearn import model_selection
from sklearn import  metrics
from statsmodels.formula.api import ols

In [171]:
model = ols("loan_status ~ I(fico_average**3)+I(purpose_small_business)", cleaned_loans).fit()

print(model.summary2())

                     Results: Ordinary least squares
Model:                 OLS                Adj. R-squared:       0.023     
Dependent Variable:    loan_status        AIC:                  26992.5239
Date:                  2022-03-27 04:40   BIC:                  27018.1696
No. Observations:      38123              Log-Likelihood:       -13493.   
Df Model:              2                  F-statistic:          458.4     
Df Residuals:          38120              Prob (F-statistic):   1.90e-197 
R-squared:             0.023              Scale:                0.11885   
--------------------------------------------------------------------------
                           Coef.  Std.Err.    t     P>|t|   [0.025  0.975]
--------------------------------------------------------------------------
Intercept                  0.5607   0.0117  47.8176 0.0000  0.5377  0.5837
I(fico_average ** 3)       0.0000   0.0000  26.1899 0.0000  0.0000  0.0000
I(purpose_small_business) -0.1374   0.0084 -16.